# Dodgers Data Bot
> This notebook is a sketchpad for data collected in this project. Nothing to see here! 

---

In [56]:
import os
import requests
import time
import pandas as pd
import jupyter_black
import altair as alt
from IPython.display import Image
from tqdm.notebook import tqdm
import altair_stiles as altstiles

In [ ]:
jupyter_black.load()
pd.options.display.max_columns = 100
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()
alt.themes.register("stiles", altstiles.theme)
alt.themes.enable("stiles")

In [96]:
def divisors(n: int):
    """Return all integer divisors of n (positive), sorted."""
    if n == 0:
        return []  # undefined; every nonzero int divides 0
    n = abs(n)
    out = set()
    d = 1
    # walk up to sqrt(n), grabbing pairs d and n//d
    while d * d <= n:
        if n % d == 0:
            out.add(d)
            out.add(n // d)
        d += 1
    return sorted(out)

---

## Fetch

#### Read historical archive, sorting by year and game

In [141]:
# Fetch past 100 seasons from archive created by scripts/29_fetch_historical_standings.py.
# Note: Team became the "Dodgers" in 1932
src = (
    pd.read_parquet(
        "https://stilesdata.com/dodgers/data/standings/dodgers_standings_1925_present.parquet"
    )
    .sort_values(by=["game_date", "gm"], ascending=[True, False])
    .reset_index(drop=True)
)

In [ ]:
# Extract the season year from the game date
src["season"] = pd.to_datetime(src["game_date"]).dt.year

In [143]:
df = src.query("season >=1926").copy()

In [145]:
# How many years?
len(df["season"].unique())

100

In [146]:
# examples
print(divisors(86))  # [1, 2, 47, 94]
print(divisors(94))  # [1]
print(divisors(100))  # [1, 97]  -> prime

[1, 2, 43, 86]
[1, 2, 47, 94]
[1, 2, 4, 5, 10, 20, 25, 50, 100]


---

## Charts

#### Facetted area chart showing games back each season

In [121]:
base = (
    alt.Chart(df.query("season >=1946"))
    .transform_calculate(
        # clip to zero in one pass
        gb_pos="datum.gb > 0 ? datum.gb : 0",
        gb_neg="datum.gb < 0 ? datum.gb : 0",
    )
    .properties(height=100, width=100)
)

x = alt.X("gm:Q", axis=alt.Axis(values=[1, 162], grid=False), title="")
y_axis = alt.Axis(values=[20, 10, 0, -10, -20, -30])
y_scale = alt.Scale(zero=False)

pos = base.mark_area(opacity=0.9).encode(
    x=x,
    y=alt.Y("gb_pos:Q", scale=y_scale, axis=y_axis, title=""),
    y2=alt.value(0),
    color=alt.value("#005a9c"),
)

neg = base.mark_area(opacity=0.9).encode(
    x=x,
    y=alt.Y("gb_neg:Q", scale=y_scale, axis=y_axis, title=""),
    y2=alt.value(0),
    color=alt.value("#ef3e42"),
)

# share the same data via `base`; alt.datum keeps it simple
zero = base.mark_rule(strokeDash=[3, 3]).encode(y=alt.datum(0))

# newest → oldest
season_order = sorted(df["season"].unique(), reverse=True)

chart = alt.layer(pos, neg, zero).facet(
    facet=alt.Facet("season:N", sort=season_order),
    columns=15,
)
chart

alt.FacetChart(...)